In [1]:
import numpy as np
f0 = 545.694068
f1 = 623.5156078
# Specify the path and filename
filename_an1 = 'an1_2025.txt'
filename_an2 = 'an2_2025.txt'
matrix =  np.array([[         np.nan, 457.74885809, 460.70069237, 463.65252665,
        466.60216223],
       [466.96523442, 469.92057413, 472.87591385, 475.83125357,
        478.78659329],
       [479.49650835, 482.45184807, 485.40592233, 488.35999659,
                 np.nan],
       [         np.nan,          np.nan, 531.90854739, 534.86038883,
        537.81045731],
       [         np.nan, 535.71541587, 538.66505145, 541.61468703,
        544.56432261],
       [539.37243953, 542.32856506, 545.282623  , 548.23445728,
        551.18629156],
       [545.79903465, 548.75437437, 551.70971409, 554.6650538 ,
                 np.nan],
       [551.93251007, 554.88784978, 557.8431895 ,          np.nan,
                 np.nan],
       [         np.nan,          np.nan,          np.nan, 593.57925724,
        596.52889282],
       [         np.nan,          np.nan, 594.63100532, 597.58214852,
        600.5317841 ],
       [         np.nan, 596.04519024, 598.9992645 , 601.95109877,
        604.90293305],
       [597.70461366, 600.65995337, 603.61408859, 606.56592286,
        609.51775714],
       [602.54187381, 605.49786766, 608.45194192, 611.40601618,
                 np.nan],
       [607.64452195, 610.59842172, 613.55249598,          np.nan,
                 np.nan],
       [613.1734413 , 616.12878102,          np.nan,          np.nan,
                 np.nan],
       [         np.nan,          np.nan,          np.nan,          np.nan,
        596.85291985],
       [         np.nan,          np.nan,          np.nan, 600.80649199,
        603.75612757],
       [         np.nan,          np.nan, 603.98153689, 606.63337117,
        609.58272399],
       [         np.nan, 606.05031215, 609.0043864 , 611.95622068,
        614.90805496],
       [608.02108391, 610.97515816, 613.92923242, 616.88150547,
        619.83099091],
       [612.56078504, 615.5148593 , 618.46893356, 621.42101298,
                 np.nan],
       [616.66311518, 619.6184549 , 622.57248451,          np.nan,
                 np.nan],
       [620.15168428, 623.107024  ,          np.nan,          np.nan,
                 np.nan],
       [620.45592666,          np.nan,          np.nan,          np.nan,
                 np.nan]])

# Read the text file and load the content into an array
matrix_an1 = np.genfromtxt(filename_an1, delimiter='\t', dtype=float)
matrix_an2 = np.genfromtxt(filename_an2, delimiter='\t', dtype=float)
# print(matrix_an1,np.shape(matrix_an2))
# Print the array to verify its content

new_matrix = f0+matrix_an2+matrix_an1*(f1-f0)
print(new_matrix)

differences = np.diff(new_matrix, axis=1)
#print(differences)
average_differences = np.nanmean(differences, axis=0)
# print(average_differences)
new_matrix[np.isnan(new_matrix)] = 0
def fill_zeros(row, spacings):
    zero_indices = np.where(row == 0)[0]
    non_zero_indices = np.where(row != 0)[0]
    
    if len(non_zero_indices) == 0:
        # If there are no non-zero elements, we cannot interpolate/extrapolate
        return row
    
    for i in range(len(row)):
        if row[i] == 0:
            # Find the nearest non-zero indices before and after the zero element
            prev_index = non_zero_indices[non_zero_indices < i][-1] if len(non_zero_indices[non_zero_indices < i]) > 0 else None
            next_index = non_zero_indices[non_zero_indices > i][0] if len(non_zero_indices[non_zero_indices > i]) > 0 else None
            
            if prev_index is not None and next_index is not None:
                # Interpolate
                row[i] = row[prev_index] + (row[next_index] - row[prev_index]) * (i - prev_index) / (next_index - prev_index)
            elif prev_index is not None:
                # Extrapolate backwards
                row[i] = row[prev_index] + spacings[prev_index] * (i - prev_index)
            elif next_index is not None:
                # Extrapolate forwards
                row[i] = row[next_index] - spacings[next_index - 1] * (next_index - i)
    
    return row
filled_matrix = np.zeros(np.shape(new_matrix))
for i, row in enumerate(new_matrix):
    filled_matrix[i] = fill_zeros(row, average_differences)
nan_positions = np.isnan(matrix)
filled_matrix[nan_positions] = np.nan
cali_freqs = filled_matrix
print(cali_freqs)

[[         nan 458.16004916 461.1135656  464.06491951          nan]
 [467.37721935          nan          nan          nan          nan]
 [479.90623096 482.86193975          nan          nan          nan]
 [         nan          nan 532.32229454 535.27356745 538.22274565]
 [         nan          nan          nan          nan 544.97570004]
 [539.78485576 542.74055856          nan          nan 551.5944991 ]
 [546.21021645          nan          nan          nan          nan]
 [552.34414299          nan          nan          nan          nan]
 [         nan          nan          nan 593.99213265          nan]
 [         nan          nan 595.04411874 597.99546365          nan]
 [         nan          nan 599.41185203          nan          nan]
 [         nan 601.07282879 604.02637923          nan          nan]
 [602.95440328 605.91015808          nan          nan          nan]
 [608.05468152 611.01041631          nan          nan          nan]
 [613.58399307          nan          nan        

In [3]:
%matplotlib widget

In [5]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from ipywidgets import interact, FloatSlider, Layout, Style

Fs = [1,2,3,4]
states = []
for i in Fs:
    for j in range(2*i+1):
        mF = i-j
        states.append([i,mF])

        

# Extract all valid (non-NaN) frequency values
rows, cols = np.indices(cali_freqs.shape)
valid = ~np.isnan(cali_freqs)
freq_values = cali_freqs[valid]
col_indices = cols[valid] - 2  # Adjust column index as before
row_indices = rows[valid]

state_label = []
for i in row_indices:
    state_label.append(states[i])

# Calculate new frequencies offset by +/- 1.351 MHz
freq_values_plus1 = freq_values + 1.46
freq_values_minus1 = freq_values - 1.46

# Calculate additional new frequencies offset by +/- 1.163 MHz
freq_values_plus2 = freq_values + 1.27
freq_values_minus2 = freq_values - 1.27

freq_values_plus3 = freq_values + 20.772
freq_values_minus3 = freq_values - 20.772


# Define colors for each column, using specific colors
column_colors = {
    -2: 'red',     # Column 0
    -1: 'green',   # Column 1
    0: 'blue',    # Column 2
    2: 'black',   # Column 3
    1: 'purple'   # Column 4
}

def plot_frequencies(center_freq, x_span):
    # Create the plot
    fig, ax = plt.subplots(figsize=(15, 7))
    
    # Function to add lines to the plot
    def add_lines(freqs, columns, rows, style, label_suffix, add_to_legend=True):
        for freq, col, row in zip(freqs, columns, rows):
            if add_to_legend:
                label = f'$S_{"{1/2}"},m_F = ${col}'
            else:
                label = None  # Exclude from legend
            # Draw the vertical line
            ax.axvline(x=freq, linestyle=style, color=column_colors.get(col, 'gray'), label=label)
            # Annotate the vertical line
            ax.annotate(f'$|F={row[0]}, m_F = {row[1]} \\rangle$', xy=(freq, 0.5), xytext=(-6, 0),
                        textcoords="offset points", ha='left', va='center',
                        fontsize=8, color=column_colors.get(col, 'gray'),rotation = -90,bbox=dict(boxstyle="round,pad=0.3", facecolor='white', edgecolor='none', alpha=0.95))

    # Add original frequencies as solid lines
    add_lines(freq_values, col_indices, state_label, '-', '')
    # Add motional modes (+1.351 MHz and +1.163 MHz) as dotted lines, not added to legend
    add_lines(freq_values_plus1, col_indices, state_label, ':', '+1.351 MHz', add_to_legend=False)
    add_lines(freq_values_plus2, col_indices, state_label, '-.', '+1.163 MHz', add_to_legend=False)
    add_lines(freq_values_plus3, col_indices, state_label, '--', '+20.761 MHz', add_to_legend=False)
    # Add motional modes (-1.351 MHz and -1.163 MHz) as dotted lines, not added to legend
    add_lines(freq_values_minus1, col_indices, state_label, ':', '-1.351 MHz', add_to_legend=False)
    add_lines(freq_values_minus2, col_indices, state_label, '-.', '-1.163 MHz', add_to_legend=False)
    add_lines(freq_values_minus3, col_indices, state_label, '--', '-20.761 MHz', add_to_legend=False)
    
    ax.set_xlim(center_freq - x_span / 2, center_freq + x_span / 2)

    ax.set_title('$S_{1/2}$ to $D_{5/2}$ Transition Frequencies with Motional Modes')
    ax.set_xlabel('Transition Frequency (MHz)')
    ax.grid(True)

    handles, labels = plt.gca().get_legend_handles_labels()
    by_label = dict(zip(labels, handles))
    ax.legend(by_label.values(), by_label.keys(), loc='upper left', bbox_to_anchor=(1, 1))


    plt.show()


slider_style = Style(handle_color='lightblue')  # You can specify the handle color

# Define layout for the sliders
slider_layout = Layout(width='1500px', height='25px')  # Adjust the width and height as needed


interact(plot_frequencies,
         center_freq=FloatSlider(value=605.114, min=min(np.concatenate([freq_values_minus1, freq_values_minus2])), 
                                 max=max(np.concatenate([freq_values_plus1, freq_values_plus2])), step=0.1, description='Center Frequency:', 
                            layout=slider_layout),
         x_span=FloatSlider(value=1, min=0.25, max=300, step=0.25, description='X Span:', 
                            layout=slider_layout))

interactive(children=(FloatSlider(value=605.114, description='Center Frequency:', layout=Layout(height='25px',…

<function __main__.plot_frequencies(center_freq, x_span)>

In [8]:
import numpy as np
hbar = 1.054_571_817e-34    # J·s
m_Ba = 2.28e-25             # kg
λ     = 1762e-9             # m  (E2 transition)
k0    = 2*np.pi/λ

def lamb_dicke(ω_trap_Hz, angle_deg):
    θ = np.deg2rad(angle_deg)
    return k0*np.sin(θ)*np.sqrt(hbar/(2*m_Ba*ω_trap_Hz))
eta_x = lamb_dicke(2*np.pi*1.27e6, 45)
eta_y = lamb_dicke(2*np.pi*1.46e6, 45)

In [10]:
n_x = 100
n_y = 100
strength_factors = np.concatenate([
    np.ones_like(freq_values),
    eta_x*np.sqrt(n_x+1)*np.ones_like(freq_values),
    eta_x*np.sqrt(n_x)*np.ones_like(freq_values),
    eta_y*np.sqrt(n_y+1)*np.ones_like(freq_values),
    eta_y*np.sqrt(n_y)*np.ones_like(freq_values)
])

In [12]:
import numpy as np
import matplotlib.pyplot as plt
from ipywidgets import interact, FloatSlider, Layout

def freq_curve_plot(cali_freqs, pi_time_matrix):
    Fs=[1,2,3,4]
    states=[(i,i-j) for i in Fs for j in range(2*i+1)]
    rows,cols=np.indices(cali_freqs.shape)
    valid=~np.isnan(cali_freqs)
    carrier_freqs=cali_freqs[valid]
    col_idx=cols[valid]-2
    row_idx=rows[valid]
    carrier_pi=pi_time_matrix[valid]
    eta_x = lamb_dicke(2*np.pi*1.27e6, 45)
    eta_y = lamb_dicke(2*np.pi*1.46e6, 45)
    n=100
    fxp,fxm=eta_x*np.sqrt(n+1),eta_x*np.sqrt(n)
    fyp,fym=eta_y*np.sqrt(n+1),eta_y*np.sqrt(n)
    side_freqs=[carrier_freqs+1.46,carrier_freqs-1.46,carrier_freqs+1.27,carrier_freqs-1.27]
    side_pi=[carrier_pi/fxp,carrier_pi/fxm,carrier_pi/fyp,carrier_pi/fym]
    all_freqs=np.concatenate([carrier_freqs]+side_freqs)
    all_pi=np.concatenate([carrier_pi]+side_pi)
    all_cols=np.concatenate([col_idx]*5)
    styles=np.concatenate([np.full_like(carrier_freqs,'-'),np.full_like(carrier_freqs,':'),np.full_like(carrier_freqs,':'),np.full_like(carrier_freqs,'-.'),np.full_like(carrier_freqs,'-.')])
    colors={-2:'red',-1:'green',0:'blue',1:'purple',2:'black'}
    Omega=np.pi/(all_pi*1e-6)
    def prob(detuning,omega,t):
        d=2*np.pi*detuning*1e6
        total=np.sqrt(omega**2+d**2)
        return (omega**2/total**2)*np.sin(total*t/2)**2
    def plot(center,xspan,res):
        freq=np.linspace(center-xspan/2,center+xspan/2,res)
        fig,ax=plt.subplots(figsize=(15,7))
        for f,o,t,s,c in zip(all_freqs,Omega,all_pi,styles,all_cols):
            ax.plot(freq,prob(freq-f,o,t*1e-6),s,color=colors.get(c,'gray'),alpha=0.8)
        ax.set_xlim(center-xspan/2,center+xspan/2)
        ax.set_xlabel('Frequency (MHz)')
        ax.set_ylabel('Excitation')
        plt.show()
    interact(plot,
             center=FloatSlider(value=carrier_freqs.mean(),min=carrier_freqs.min()-1,max=carrier_freqs.max()+1,step=0.1,layout=Layout(width='1500px')),
             xspan=FloatSlider(value=2,min=0.25,max=20,step=0.25,layout=Layout(width='1500px')),
             res=FloatSlider(value=1000,min=200,max=5000,step=100,layout=Layout(width='1500px')))


In [14]:
import numpy as np 
from scipy.io import loadmat
transition_strengths = np.array([[np.nan, 0.0563, 0.055, 0.0519, 0.0341],
                        [0.0753, 0.0246, 0.0096, 0.0336, 0.056],
                        [0.053, 0.0598, 0.047, 0.0355, np.nan],
                        [np.nan, np.nan, 0.1103, 0.1061, 0.0819],
                        [np.nan, 0.1273, 0.0275, 0.0613, 0.0981],
                        [0.0973, 0.0635, 0.0919, 0.0258, 0.0932],
                        [0.1163, 0.0281, 0.0575, 0.107, np.nan],
                        [0.1105, 0.1056, 0.0814, np.nan, np.nan],
                        [np.nan, np.nan, np.nan, 0.2813, 0.0091],
                        [np.nan, np.nan, 0.2288, 0.1549, 0.0415],
                        [np.nan, 0.1517, 0.2135, 0.0697, 0.0446],
                        [0.0763, 0.2008, 0.1741, 0.003, 0.0359],
                        [0.1367, 0.2351, 0.0773, 0.039, np.nan],
                        [0.2241, 0.1763, 0.0106, np.nan, np.nan],
                        [0.268, 0.0634, np.nan, np.nan, np.nan],
                        [np.nan, np.nan, np.nan, np.nan, 0.3278],
                        [np.nan, np.nan, np.nan, 0.0828, 0.268],
                        [np.nan, np.nan, 0.0019, 0.1664, 0.234],
                        [np.nan, 0.025, 0.0679, 0.2278, 0.1523],
                        [0.0232, 0.001, 0.156, 0.2077, 0.0915],
                        [0.0309, 0.0593, 0.206, 0.1694, np.nan],
                        [0.0276, 0.1438, 0.2401, np.nan, np.nan],
                        [0.0094, 0.2862, np.nan, np.nan, np.nan],
                        [0.3278, np.nan, np.nan, np.nan, np.nan]])

import numpy as np

transition_strengths = np.loadtxt('Z:\Lab Data\Phase_and_freq_correction_180Hz\Transition_strengths_4p216.txt',delimiter=',')  # Assumes space-delimited file
transition_strengths[transition_strengths == 0] = np.nan
# print(transition_strengths)


pi_t = [18.622, 31.746, 37.865, 27.596, 36.429]
strengths = np.array([transition_strengths[23,0],transition_strengths[14,0],transition_strengths[17,4],transition_strengths[16,4],transition_strengths[15,4]])
pitime_n2 = pi_t[0] # [-2, 4, -4]
pitime_n1 = pi_t[1] # [-2, 3, -3]
pitime_0 = pi_t[2] # [2, 4, 2]
pitime_p1 = pi_t[3] # [2, 4, 3]
pitime_p2 = pi_t[4] # [2, 4, 4]

pi_t = np.array([pitime_n2,pitime_n1,pitime_0,pitime_p1,pitime_p2])
factors = pi_t * strengths
Fs = [1,2,3,4]
row_labels = []
for i in Fs:
    for j in range(2*i+1):
        mF = i-j
        row_labels.append([i,mF])
col_labels = [-2, -1, 0, 1, 2]

pi_times = np.zeros((24,5))
for i in range(np.shape(transition_strengths)[0]):
    for j in range(np.shape(transition_strengths)[1]):
        # print(i,j)
        if not np.isnan(transition_strengths[i,j]):

            delta_m = (row_labels[i][1]-col_labels[j])+2

            pi_times[i,j] = factors[delta_m]/transition_strengths[i,j]
print(pi_times)

[[   0.          211.9322501   134.46824927  170.80710206  249.8197383 ]
 [ 158.67999176  301.16549727  921.45526918  253.17624047  108.98500926]
 [ 139.52333084  148.14607451  181.16403349  171.87311245    0.        ]
 [   0.            0.          108.23055675   69.68854243  108.16046645]
 [   0.           93.77573445  268.8374713   144.6413757    86.74807471]
 [ 122.70543703  116.4129164    96.40360429  329.79550561   65.47951644]
 [  63.61091827  314.75453041  147.92715683   57.05244149    0.        ]
 [  80.1717235    80.57107542   75.00681767    0.            0.        ]
 [   0.            0.            0.           42.44279842  816.89796011]
 [   0.            0.           52.18745061   47.73855147  213.54373172]
 [   0.           78.71729484   34.64748359  127.12049517  190.86212989]
 [ 156.52264106   36.83116196   50.89949487 2802.28634035  170.05153014]
 [  54.1229026    37.67897927  110.12364584  156.61516797    0.        ]
 [  39.54078846   48.26913817  577.36344243    0.  

In [20]:
freq_curve_plot(cali_freqs = cali_freqs, pi_time_matrix = pi_times)

interactive(children=(FloatSlider(value=571.9256904381834, description='Center (MHz)', layout=Layout(width='15…

In [18]:
import numpy as np
import matplotlib.pyplot as plt
from ipywidgets import interact, FloatSlider, Layout


def freq_curve_plot(cali_freqs, pi_time_matrix, n_bar=100, eta_x=0.0127, eta_y=0.0136):
    """Interactive frequency‑sweep plot.

    Parameters
    ----------
    cali_freqs : 2‑D ndarray (MHz)
        Calibrated carrier transition frequencies (NaN for unused cells).
    pi_time_matrix : 2‑D ndarray (µs)
        π‑times for each carrier transition (same shape as cali_freqs).
    n_bar : float, optional
        Mean phonon number used for Lamb–Dicke scaling (default 100).
    eta_x, eta_y : float, optional
        Lamb–Dicke factors for x‑ and y‑modes (default 0.0127, 0.0136).
    """

    # build (F, mF) lookup – not used directly but kept for future annotations
    Fs = [1, 2, 3, 4]
    states = [(F, F - j) for F in Fs for j in range(2 * F + 1)]

    # carrier subset (non‑NaN entries)
    rows, cols = np.indices(cali_freqs.shape)
    valid = ~np.isnan(cali_freqs)

    carrier_freqs = cali_freqs[valid]          # MHz
    carrier_pi = pi_time_matrix[valid]         # µs
    col_idx = cols[valid] - 2                  # S‑manifold m_F mapping

    # Lamb‑Dicke scaling factors for ±1st‑order side‑bands
    fxp, fxm = eta_x * np.sqrt(n_bar + 1), eta_x * np.sqrt(n_bar)
    fyp, fym = eta_y * np.sqrt(n_bar + 1), eta_y * np.sqrt(n_bar)

    side_freqs = [carrier_freqs + 1.46, carrier_freqs - 1.46,
                  carrier_freqs + 1.27, carrier_freqs - 1.27]
    side_pi = [carrier_pi / fxp, carrier_pi / fxm,
               carrier_pi / fyp, carrier_pi / fym]

    # concatenate carriers + side‑bands
    all_freqs = np.concatenate([carrier_freqs] + side_freqs)
    all_pi = np.concatenate([carrier_pi] + side_pi)
    all_cols = np.concatenate([col_idx] * 5)

    # per‑curve line‑style vector (solid for carriers, dotted/dash‑dot for side‑bands)
    styles = np.concatenate([
        np.repeat('-', len(carrier_freqs)),    # carriers
        np.repeat(':', len(carrier_freqs)),    # +x
        np.repeat(':', len(carrier_freqs)),    # –x
        np.repeat('-.', len(carrier_freqs)),   # +y
        np.repeat('-.', len(carrier_freqs))    # –y
    ])

    colors = { -2: 'red', -1: 'green', 0: 'blue', 1: 'purple', 2: 'black' }

    # Rabi frequency (rad/s) from π‑time (µs)
    Omega = np.pi / (all_pi * 1e-6)

    def prob(detuning, omega, t):
        """Two‑level excitation probability at time t (s)."""
        delta = 2 * np.pi * detuning * 1e6      # MHz → rad/s
        total = np.sqrt(omega ** 2 + delta ** 2)
        return (omega ** 2 / total ** 2) * np.sin(total * t / 2) ** 2

    def plot(center, span, pts):
        sweep = np.linspace(center - span / 2, center + span / 2, int(pts))
        fig, ax = plt.subplots(figsize=(15, 7))

        for f0, om, t_pi, style, col in zip(all_freqs, Omega, all_pi, styles, all_cols):
            ax.plot(sweep, prob(sweep - f0, om, t_pi * 1e-6),
                    linestyle=style, color=colors.get(col, 'gray'), alpha=0.85)

        ax.set_xlim(center - span / 2, center + span / 2)
        ax.set_xlabel('Frequency (MHz)')
        ax.set_ylabel('Excitation probability')
        ax.set_title('Frequency sweep at π‑times\nCarriers (solid) and first‑order secular side‑bands')
        ax.grid(True)
        plt.show()

    # interactive sliders
    interact(
        plot,
        center=FloatSlider(value=float(carrier_freqs.mean()),
                           min=float(carrier_freqs.min() - 1),
                           max=float(carrier_freqs.max() + 1),
                           step=0.1, description='Center (MHz)',
                           layout=Layout(width='1500px')),
        span=FloatSlider(value=2, min=0.25, max=20, step=0.25,
                         description='Span (MHz)',
                         layout=Layout(width='1500px')),
        pts=FloatSlider(value=1000, min=200, max=5000, step=100,
                        description='Points',
                        layout=Layout(width='1500px')))
